In [ ]:
# ..... get pseudobulk matrices across stages ..... #

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)

In [3]:
# get pseudo-bulk for CPM data
get_cpm_pseudo_bulk <- function(scdata, ctype_list){      
        
    new_labels = scdata$ctypes
    nbds = unique(new_labels)
    nbds <- nbds[which(!is.na(nbds) & nbds!='unassigned')]
    sc_sub2 = matrix(NA, nrow = dim(scdata)[1], ncol = length(nbds))
    
    for (i in 1:length(nbds)){
        cols = which(new_labels==nbds[i])
    
        if(length(cols)>1){
            sc_sub2[,i] = rowSums(cpm(scdata)[,cols])/length(cols)
        }else if(length(cols)==1){            
            sc_sub2[,i] = cpm(scdata)[,cols]
        }else{
            sc_sub2[,i] = NA
        }
    }    
    rownames(sc_sub2) = rownames(scdata)
    colnames(sc_sub2) = nbds
    return(sc_sub2[,ctype_list])
}

In [4]:
# cell type order
# ctype_order = c('vCM', 'aCM', 'immature-CM', 'endothelial', 'endocardial', 'epicardial',
                # 'fibroblast', 'SMC', 'pericyte', 'neural-crest', 'blood', 'macrophage')

ctype_order = c('LV_vCM', 'RV_vCM', 'aCM', 'immature_CM', 'endocardial', 'epicardial',
                'mes_progenitor', 'fibroblast', 'SMC', 'neural_crest', 'blood', 'macrophage')
length(ctype_order)

[1] 12

In [5]:
# load integrated data
sc1 = readRDS('turtle_integrated_ssSTACAS.rds')
DefaultAssay(sc1) <- 'RNA'

# get harmonised labels
tab1 = read.delim('turtle_ssSTACAS_celltypes.txt', sep = '\t')
tab1[1,]

sc1$stage = sc1$orig.ident
sc1$broad_type = tab1$subtype[match(sc1$seurat_clusters, tab1$cluster)]
sc1$cluster = tab1$label[match(sc1$seurat_clusters, tab1$cluster)]
sc1$ctypes <- sc1$cluster  # sub('\\_.*', '', sc1$cluster)
sc1@meta.data[1,]

species cluster celltype    subtype     label       cluster_new
1 turtle  0       Endocardial endocardial endocardial c1

orig.ident nCount_RNA nFeature_RNA species
stage14_sample4_AAACCCACAATGAACA-1 stage14    3281       1926         turtle 
                                   dataset         consensus_type  
stage14_sample4_AAACCCACAATGAACA-1 stage14_sample4 Endothelial_cell
                                   integrated_snn_res.1 seurat_clusters stage  
stage14_sample4_AAACCCACAATGAACA-1 4                    4               stage14
                                   broad_type  cluster     ctypes     
stage14_sample4_AAACCCACAATGAACA-1 endocardial endocardial endocardial

In [6]:
# make SCE object
sce2 = SingleCellExperiment(list(counts = sc1@assays$RNA@counts), colData = DataFrame(sc1@meta.data))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))
sce2

class: SingleCellExperiment 
dim: 26985 68775 
metadata(0):
assays(2): counts cpm
rownames(26985): OTX2 LOC101934893 ... MT-ND6 MT-CYTB
rowData names(0):
colnames(68775): stage14_sample4_AAACCCACAATGAACA-1
  stage14_sample4_AAACCCATCGCTATTT-1 ...
  stage21_sample2_TTTGTTGTCATGCGGC-1 stage21_sample2_TTTGTTGTCATTGCGA-1
colData names(12): orig.ident nCount_RNA ... cluster ctypes
reducedDimNames(0):
mainExpName: NULL
altExpNames(0):

In [7]:
# create pseudo-bulk matrices for all genes
scbulk1 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage14'], ctype_order)
scbulk2 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage17'], ctype_order)
scbulk3 = get_cpm_pseudo_bulk(sce2[,sce2$stage=='stage21'], ctype_order)

scbulk1[c('TBX5','COL3A1'),]

LV_vCM    RV_vCM    aCM        immature_CM endocardial epicardial
TBX5   430.06955 133.94444 1201.77360 212.2669     23.13788    61.21563 
COL3A1  33.35229  58.75402   33.46578 192.3616    576.60389   200.77595 
       mes_progenitor fibroblast SMC       neural_crest blood     macrophage
TBX5    30.6968       198.42630   13.08294  0.00000      6.953442  8.712011 
COL3A1 234.9844        84.60028  245.46293 21.06771     37.462747 86.164485

In [8]:
# save
save(scbulk1, scbulk2, scbulk3, file = 'turtle_integrated_pseudobulk_expression_matrices.Rdata')

In [9]:
colnames(scbulk1) <- paste0('s1|', colnames(scbulk1))
colnames(scbulk2) <- paste0('s2|', colnames(scbulk2))
colnames(scbulk3) <- paste0('s3|', colnames(scbulk3))

dfnew = cbind(scbulk1, scbulk2, scbulk3)

# save
save(dfnew, file = 'turtle_full_integrated_pseudobulk_expression_matrix.Rdata')